In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import cv2
import os
import glob
from utils.experiments_functions import get_img_info_simple
import utils.noise_generator as noise_gen
import utils.utils as utils_functions

## Generate data

In [ ]:
# Reads 1 image from each class
images_path = f'data/Sintorn/hardware'
rot = 'r000'
seg = 's001'
images_filenames = []
for file in os.listdir(images_path):
    if file.endswith(f"{rot}-{seg}.png"):
        images_filenames.append(file)
print(len(images_filenames))
print(images_filenames)

25
['canesugar01-r000-s001.png', 'canvas01-r000-s001.png', 'couscous01-r000-s001.png', 'fabric01-r000-s001.png', 'fabric02-r000-s001.png', 'fabric03-r000-s001.png', 'fabric04-r000-s001.png', 'fabric05-r000-s001.png', 'flaxseed01-r000-s001.png', 'knitwear01-r000-s001.png', 'knitwear02-r000-s001.png', 'knitwear03-r000-s001.png', 'lentils01-r000-s001.png', 'oatmeal01-r000-s001.png', 'pearlsugar01-r000-s001.png', 'rice01-r000-s001.png', 'rug01-r000-s001.png', 'ryeflakes01-r000-s001.png', 'seeds01-r000-s001.png', 'seeds02-r000-s001.png', 'sprinkles01-r000-s001.png', 'tile01-r000-s001.png', 'towel01-r000-s001.png', 'wheat01-r000-s001.png', 'wool01-r000-s001.png']


In [4]:
# Sintorn images
all_images = {}

# Display the images
for i, filename in enumerate(images_filenames):
    print(f'Processing image {i+1}/{len(images_filenames)}: {filename}')
    # Reads image
    gs_image = cv2.imread(f'{images_path}/{filename}', cv2.IMREAD_GRAYSCALE)
    gs_image = utils_functions.normalize_uint8_to_float64(gs_image)
    
    # Adds image to the all_images dictionary
    item = filename.split('.')[0]
    if item not in all_images:
        all_images[item] = gs_image

Processing image 1/25: canesugar01-r000-s001.png
Processing image 2/25: canvas01-r000-s001.png
Processing image 3/25: couscous01-r000-s001.png
Processing image 4/25: fabric01-r000-s001.png
Processing image 5/25: fabric02-r000-s001.png
Processing image 6/25: fabric03-r000-s001.png
Processing image 7/25: fabric04-r000-s001.png
Processing image 8/25: fabric05-r000-s001.png
Processing image 9/25: flaxseed01-r000-s001.png
Processing image 10/25: knitwear01-r000-s001.png
Processing image 11/25: knitwear02-r000-s001.png
Processing image 12/25: knitwear03-r000-s001.png
Processing image 13/25: lentils01-r000-s001.png
Processing image 14/25: oatmeal01-r000-s001.png
Processing image 15/25: pearlsugar01-r000-s001.png
Processing image 16/25: rice01-r000-s001.png
Processing image 17/25: rug01-r000-s001.png
Processing image 18/25: ryeflakes01-r000-s001.png
Processing image 19/25: seeds01-r000-s001.png
Processing image 20/25: seeds02-r000-s001.png
Processing image 21/25: sprinkles01-r000-s001.png
Proc

In [5]:
# Process all images
noise_types = ['original', 'salt_and_pepper', 'speckle', 'gaussian', 'poisson']

# sets the probabilities used
noise_param_sp = [0.15, 0.25, 0.4, 0.5] # salt and pepper
noise_param_gaussian = [0.1, 0.3, 0.8, 1.  ] # gaussian
noise_param_speckle = [0.2, 0.6, 1., 1.5 ] # speckle
noise_param_poisson = [0.5, 1.0, 6.0, 20.0] # poisson

image_data_list = []
for i, item in enumerate(all_images):
    print(f"Processing image {i+1}/{len(all_images)}: {item}")
    # get image
    gs_image = all_images[item]
    img_filename = item
    # extract metrics
    print("\tExtracting data")
    image_data = get_img_info_simple(gs_image)
    # add the information
    image_data['image_name'] = img_filename
    image_data['noise_type'] = 'original'
    image_data['noise_param'] = 0
    image_data_list.append(image_data)
    # adds no noise information to each noise_type
    for n_type in noise_types:
        if n_type != 'original':
            # adds the information
            image_data = image_data.copy()
            image_data['noise_type'] = n_type
            image_data_list.append(image_data)

    # adds s&p noise
    print("\tAdding S&P noise")
    for prob in noise_param_sp:
        print(f"\t\tProbability = {prob}")
        # generate noise image
        print("\t\tGenerating noised image")
        noised_image = noise_gen.add_sp_noise(gs_image, prob, prob)
        # extract metrics
        print("\t\tExtracting data")
        noised_image_data = get_img_info_simple(noised_image)
        # add the information
        noised_image_data['image_name'] = img_filename
        noised_image_data['noise_type'] = 'salt_and_pepper'
        noised_image_data['noise_param'] = prob
        image_data_list.append(noised_image_data)
    # adds gaussian noise
    print("\tAdding Gaussian noise")
    for param in noise_param_gaussian:
        print(f"\t\tSigma = {param}")
        # generate noise image
        print("\t\tGenerating noised image")
        noised_image = noise_gen.add_gaussian_noise(image=gs_image, mean=0, sigma=param)
        # extract metrics
        print("\t\tExtracting data")
        noised_image_data = get_img_info_simple(noised_image)
        # add the information
        noised_image_data['image_name'] = img_filename
        noised_image_data['noise_type'] = 'gaussian'
        noised_image_data['noise_param'] = param
        image_data_list.append(noised_image_data)
    # adds speckle noise
    print("\tAdding Speckle noise")
    for param in noise_param_speckle:
        print(f"\t\tSigma = {param}")
        # generate noise image
        print("\t\tGenerating noised image")
        noised_image = noise_gen.add_speckle_noise(gs_image, mean=0, sigma=param)
        # extract metrics
        print("\t\tExtracting data")
        noised_image_data = get_img_info_simple(noised_image)
        # add the information
        noised_image_data['image_name'] = img_filename
        noised_image_data['noise_type'] = 'speckle'
        noised_image_data['noise_param'] = param
        image_data_list.append(noised_image_data)
    # adds poisson noise
    print("\tAdding Poisson noise")
    for factor in noise_param_poisson:
        print(f"\t\tFactor = {factor}")
        # generate noise image
        print("\t\tGenerating noised image")
        noised_image = noise_gen.add_poisson_noise_normalized(gs_image, factor)
        # extract metrics
        print("\t\tExtracting data")
        noised_image_data = get_img_info_simple(noised_image)
        # add the information
        noised_image_data['image_name'] = img_filename
        noised_image_data['noise_type'] = 'poisson'
        noised_image_data['noise_param'] = factor
        image_data_list.append(noised_image_data)

Processing image 1/25: canesugar01-r000-s001
	Extracting data
	Adding S&P noise
		Probability = 0.15
		Generating noised image
		Extracting data
		Probability = 0.25
		Generating noised image
		Extracting data
		Probability = 0.4
		Generating noised image
		Extracting data
		Probability = 0.5
		Generating noised image
		Extracting data
	Adding Gaussian noise
		Sigma = 0.1
		Generating noised image
		Extracting data
		Sigma = 0.3
		Generating noised image
		Extracting data
		Sigma = 0.8
		Generating noised image
		Extracting data
		Sigma = 1.0
		Generating noised image
		Extracting data
	Adding Speckle noise
		Sigma = 0.2
		Generating noised image
		Extracting data
		Sigma = 0.6
		Generating noised image
		Extracting data
		Sigma = 1.0
		Generating noised image
		Extracting data
		Sigma = 1.5
		Generating noised image
		Extracting data
	Adding Poisson noise
		Factor = 0.5
		Generating noised image
		Extracting data
		Factor = 1.0
		Generating noised image
		Extracting data
		Factor = 6.

In [6]:
data_default_aux = pd.concat(image_data_list, ignore_index=True)
data_default_aux.to_csv(f"results/qualificacao_noises/sintorn_noises/sintorn_noises.csv", index=False)

## Generate data for all images from class

In [5]:
# Path to the directory
images_path = f'data/Sintorn/hardware/'
images_class = 'fabric04'

# Get all files with the prefix <images_class> in the directory
images_full_path = glob.glob(f"{images_path}*{images_class}*")

# Extract just the filenames without the path
images_filenames = [os.path.basename(path) for path in images_full_path]

print(f"Found {len(images_filenames)} files with prefix '{images_class}'")
print("First 5 filenames:", images_filenames[:5] if len(images_filenames) >= 5 else images_filenames)


Found 900 files with prefix 'fabric04'
First 5 filenames: ['fabric04-r000-s001.png', 'fabric04-r000-s002.png', 'fabric04-r000-s003.png', 'fabric04-r000-s004.png', 'fabric04-r000-s005.png']


In [6]:
# Process all images
noise_types = ['original', 'salt_and_pepper', 'speckle', 'gaussian', 'poisson']
# Class names used in the experiment
image_classes = ['seeds02', 'fabric03', 'canesugar01', 'couscous01', 'fabric04']

# sets the probabilities used
noise_param_sp = [0.15, 0.25, 0.4, 0.5] # salt and pepper
noise_param_gaussian = [0.1, 0.3, 0.8, 1.  ] # gaussian
noise_param_speckle = [0.2, 0.6, 1., 1.5 ] # speckle
noise_param_poisson = [0.5, 1.0, 6.0, 20.0] # poisson

image_data_list = []

images_path = f'data/Sintorn/hardware/'
for images_class in image_classes:
    print(f"Processing images of class: {images_class}")
    # Get all files with the prefix <images_class> in the directory
    images_full_path = glob.glob(f"{images_path}*{images_class}*")

    # Extract just the filenames without the path
    images_filenames = [os.path.basename(path) for path in images_full_path]

    print(f"Found {len(images_filenames)} files with prefix '{images_class}'")
    # print("First 5 filenames:", images_filenames[:5] if len(images_filenames) >= 5 else images_filenames)

    for idx, img_filename in enumerate(images_filenames):
        # reads the image
        gs_image = cv2.imread(f'{images_path}/{img_filename}', cv2.IMREAD_GRAYSCALE)
        image_title = img_filename.split('.')[0]
        print(image_title, f"{idx+1}/{len(images_filenames)}")
        # normalize the image	
        gs_image = utils_functions.normalize_uint8_to_float64(gs_image)
        # extract metrics
        print("\tExtracting data")
        image_data = get_img_info_simple(gs_image)
        # add the information
        image_data['image_name'] = img_filename
        image_data['image_class'] = images_class
        image_data['noise_type'] = 'original'
        image_data['noise_param'] = 0
        image_data_list.append(image_data)
        # adds no noise information to each noise_type
        for n_type in noise_types:
            if n_type != 'original':
                # adds the information
                image_data = image_data.copy()
                image_data['noise_type'] = n_type
                image_data_list.append(image_data)

        # adds s&p noise
        print("\tAdding S&P noise")
        for prob in noise_param_sp:
            print(f"\t\tProbability = {prob}")
            # generate noise image
            print("\t\tGenerating noised image")
            noised_image = noise_gen.add_sp_noise(gs_image, prob, prob)
            # extract metrics
            print("\t\tExtracting data")
            noised_image_data = get_img_info_simple(noised_image)
            # add the information
            noised_image_data['image_name'] = img_filename
            noised_image_data['image_class'] = images_class
            noised_image_data['noise_type'] = 'salt_and_pepper'
            noised_image_data['noise_param'] = prob
            image_data_list.append(noised_image_data)
        # adds gaussian noise
        print("\tAdding Gaussian noise")
        for param in noise_param_gaussian:
            print(f"\t\tSigma = {param}")
            # generate noise image
            print("\t\tGenerating noised image")
            noised_image = noise_gen.add_gaussian_noise(image=gs_image, mean=0, sigma=param)
            # extract metrics
            print("\t\tExtracting data")
            noised_image_data = get_img_info_simple(noised_image)
            # add the information
            noised_image_data['image_name'] = img_filename
            noised_image_data['image_class'] = images_class
            noised_image_data['noise_type'] = 'gaussian'
            noised_image_data['noise_param'] = param
            image_data_list.append(noised_image_data)
        # adds speckle noise
        print("\tAdding Speckle noise")
        for param in noise_param_speckle:
            print(f"\t\tSigma = {param}")
            # generate noise image
            print("\t\tGenerating noised image")
            noised_image = noise_gen.add_speckle_noise(gs_image, mean=0, sigma=param)
            # extract metrics
            print("\t\tExtracting data")
            noised_image_data = get_img_info_simple(noised_image)
            # add the information
            noised_image_data['image_name'] = img_filename
            noised_image_data['image_class'] = images_class
            noised_image_data['noise_type'] = 'speckle'
            noised_image_data['noise_param'] = param
            image_data_list.append(noised_image_data)
        # adds poisson noise
        print("\tAdding Poisson noise")
        for factor in noise_param_poisson:
            print(f"\t\tFactor = {factor}")
            # generate noise image
            print("\t\tGenerating noised image")
            noised_image = noise_gen.add_poisson_noise_normalized(gs_image, factor)
            # extract metrics
            print("\t\tExtracting data")
            noised_image_data = get_img_info_simple(noised_image)
            # add the information
            noised_image_data['image_name'] = img_filename
            noised_image_data['image_class'] = images_class
            noised_image_data['noise_type'] = 'poisson'
            noised_image_data['noise_param'] = factor
            image_data_list.append(noised_image_data)

Processing images of class: seeds02
Found 900 files with prefix 'seeds02'
seeds02-r000-s001 1/900
	Extracting data
	Adding S&P noise
		Probability = 0.15
		Generating noised image
		Extracting data
		Probability = 0.25
		Generating noised image
		Extracting data
		Probability = 0.4
		Generating noised image
		Extracting data
		Probability = 0.5
		Generating noised image
		Extracting data
	Adding Gaussian noise
		Sigma = 0.1
		Generating noised image
		Extracting data
		Sigma = 0.3
		Generating noised image
		Extracting data
		Sigma = 0.8
		Generating noised image
		Extracting data
		Sigma = 1.0
		Generating noised image
		Extracting data
	Adding Speckle noise
		Sigma = 0.2
		Generating noised image
		Extracting data
		Sigma = 0.6
		Generating noised image
		Extracting data
		Sigma = 1.0
		Generating noised image
		Extracting data
		Sigma = 1.5
		Generating noised image
		Extracting data
	Adding Poisson noise
		Factor = 0.5
		Generating noised image
		Extracting data
		Factor = 1.0
		Ge

In [ ]:
data_default_aux = pd.concat(image_data_list, ignore_index=True)
data_default_aux.to_csv(f"results/qualificacao_noises/sintorn_noises/class_analysis/class_analysis.csv", index=False)